#### def developer( desarrollador : str ): Cantidad de items y porcentaje de contenido Free por año según empresa desarrolladora.

In [8]:
import pandas as pd

# Leer el archivo CSV
df = pd.read_csv('output_steam_games.csv')

# Convertir la columna 'release_date' a tipo datetime
df['release_date'] = pd.to_datetime(df['release_date'])

# Extraer el año de la fecha de lanzamiento
df['year'] = df['release_date'].dt.year

# Determinar si el juego es gratuito o no según la columna 'tags'
df['free'] = df['tags'].str.contains('Free', case=False)

# Agrupar por año y desarrollador, y calcular la cantidad de items y el porcentaje de contenido free
resultados = df.groupby(['year', 'developer']).agg(
    cantidad_de_items=('item_id', 'count'),
    contenido_free=('free', 'mean')  # Calculamos el porcentaje promedio de contenido free
).reset_index()

# Formatear el porcentaje de contenido free como porcentaje
resultados['contenido_free'] = resultados['contenido_free'].mul(100).round(2).astype(str) + '%'

# Mostrar los resultados
print(resultados)



         year                   developer  cantidad_de_items contenido_free
0      1983.0        Digital Leisure Inc.                  1           0.0%
1      1984.0        Digital Leisure Inc.                  1           0.0%
2      1984.0  Ed Hobbs,Robert Crossfield                  1           0.0%
3      1985.0    MicroProse Software, Inc                  1           0.0%
4      1986.0         Choose Multiple LLC                  1           0.0%
...       ...                         ...                ...            ...
14777  2018.0                杭州分浪网络科技有限公司                  1         100.0%
14778  2019.0           Ninetales Studios                  1           0.0%
14779  2019.0         Nodding Heads Games                  1           0.0%
14780  2019.0      Poetic Justice Studios                  1           0.0%
14781  2021.0              Freebird Games                  1           0.0%

[14782 rows x 4 columns]


#### def userdata( User_id : str ):  Debe devolver cantidad de dinero gastado por el usuario, el porcentaje de recomendación en base a reviews.recommend y cantidad de items.
##### Ejemplo de retorno: {"Usuario X" : us213ndjss09sdf, "Dinero gastado": 200 USD, "% de recomendación": 20%, "cantidad de items": 5}

In [20]:
import pandas as pd

# Cargar los datos de los usuarios, los juegos y las revisiones
user_items_df = pd.read_csv('australian_users_items.csv')
steam_games_df = pd.read_csv('output_steam_games.csv')
user_reviews_df = pd.read_csv('user_reviews.csv')

# Calcular el dinero gastado por usuario
user_money_spent = user_items_df.groupby('user_id')['item_id'].apply(lambda x: steam_games_df.loc[steam_games_df['item_id'].isin(x), 'price'].sum())

# Calcular el porcentaje de recomendación promedio por usuario
user_recommendation_percentage = user_reviews_df.groupby('user_id')['recommend'].mean() * 100

# Contar la cantidad de items por usuario
user_items_count = user_items_df['user_id'].value_counts()

# Combinar los resultados en un DataFrame único
results_df = pd.DataFrame({
    'Dinero gastado': user_money_spent,
    '% de recomendación': user_recommendation_percentage,
    'Cantidad de items': user_items_count
})

# Convertir el DataFrame a un diccionario de Python
results_dict = results_df.to_dict(orient='index')

# Imprimir los resultados
for user_id, values in results_dict.items():
    print(f'Usuario {user_id}: {values}')


Usuario --000--: {'Dinero gastado': nan, '% de recomendación': 100.0, 'Cantidad de items': nan}
Usuario --ace--: {'Dinero gastado': nan, '% de recomendación': 100.0, 'Cantidad de items': nan}
Usuario -2SV-vuLB-Kg: {'Dinero gastado': 437.49000000000007, '% de recomendación': nan, 'Cantidad de items': 68.0}
Usuario -Beave-: {'Dinero gastado': nan, '% de recomendación': 100.0, 'Cantidad de items': nan}
Usuario -I_AM_EPIC-: {'Dinero gastado': nan, '% de recomendación': 100.0, 'Cantidad de items': nan}
Usuario -Kenny: {'Dinero gastado': nan, '% de recomendación': 100.0, 'Cantidad de items': nan}
Usuario -SEVEN-: {'Dinero gastado': nan, '% de recomendación': 77.77777777777779, 'Cantidad de items': nan}
Usuario -SatansLittleHelper-: {'Dinero gastado': nan, '% de recomendación': 100.0, 'Cantidad de items': nan}
Usuario -Thyme-: {'Dinero gastado': nan, '% de recomendación': 100.0, 'Cantidad de items': nan}
Usuario -Zovix-: {'Dinero gastado': nan, '% de recomendación': 100.0, 'Cantidad de items'

#### def UserForGenre( genero : str ): Debe devolver el usuario que acumula más horas jugadas para el género dado y una lista de la acumulación de horas jugadas por año de lanzamiento.
##### Ejemplo de retorno: {"Usuario con más horas jugadas para Género X" : us213ndjss09sdf, "Horas jugadas":[{Año: 2013, Horas: 203}, {Año: 2012, Horas: 100}, {Año: 2011, Horas: 23}]}

In [3]:
import pandas as pd

def cargar_datos():
    # Carga de datos
    user_reviews = pd.read_csv('user_reviews.csv')
    australian_users_items = pd.read_csv('australian_users_items.csv')
    output_steam_games = pd.read_csv('output_steam_games.csv')

    # Conversiones de tipos necesarias
    user_reviews['item_id'] = user_reviews['item_id'].astype(str)
    australian_users_items['item_id'] = australian_users_items['item_id'].astype(str)
    output_steam_games['item_id'] = output_steam_games['item_id'].astype(str)

    return user_reviews, australian_users_items, output_steam_games

def analizar_datos(user_reviews, australian_users_items, output_steam_games, target_genre):
    # Fusión de los dataframes
    merged = pd.merge(australian_users_items, output_steam_games, on='item_id')
    merged = pd.merge(merged, user_reviews[['user_id', 'item_id']], on='item_id')

    # Evaluar los géneros correctamente
    merged['genres'] = merged['genres'].apply(lambda x: eval(x))

    # Filtrar por género
    genre_data = merged[merged['genres'].apply(lambda g: target_genre in g)]

    # Convertir release_date a formato de fecha y manejar posibles errores
    genre_data['release_date'] = pd.to_datetime(genre_data['release_date'], errors='coerce')

    # Extraer año de la fecha de lanzamiento
    genre_data['release_year'] = genre_data['release_date'].dt.year

    # Calcular el usuario con más horas jugadas para el género
    user_hours = genre_data.groupby('user_id')['playtime_forever'].sum()
    max_user = user_hours.idxmax()
    max_hours = user_hours.max()

    # Calcular las horas jugadas por año
    hours_by_year = genre_data.groupby('release_year')['playtime_forever'].sum().reset_index()
    hours_by_year = hours_by_year.rename(columns={'release_year': 'Año', 'playtime_forever': 'Horas'})

    return {
        "Usuario con más horas jugadas para Género X": max_user,
        "Horas jugadas": hours_by_year.to_dict(orient='records')
    }

def main():
    user_reviews, australian_users_items, output_steam_games = cargar_datos()
    target_genre = 'Action'
    resultados = analizar_datos(user_reviews, australian_users_items, output_steam_games, target_genre)
    print(resultados)

main()



KeyError: 'release_date'

#### def best_developer_year( año : int ): Devuelve el top 3 de desarrolladores con juegos MÁS recomendados por usuarios para el año dado. (reviews.recommend = True y comentarios positivos)
##### Ejemplo de retorno: [{"Puesto 1" : X}, {"Puesto 2" : Y},{"Puesto 3" : Z}]

In [18]:
import pandas as pd

def obtener_top_desarrolladores_por_anio(archivo_juegos, archivo_reviews, anio_dado):
    # Cargar datos de los archivos CSV
    juegos = pd.read_csv(archivo_juegos)
    reviews = pd.read_csv(archivo_reviews)

    # Convertir 'release_date' a tipo fecha
    juegos['release_date'] = pd.to_datetime(juegos['release_date'])

    # Filtrar juegos por el año dado
    juegos_anio_dado = juegos[juegos['release_date'].dt.year == anio_dado]

    # Obtener los juegos únicos del año dado
    juegos_unicos_anio_dado = juegos_anio_dado['item_id'].unique()

    # Contar la cantidad de juegos recomendados por desarrollador para cada año
    desarrolladores_por_anio = {}
    for juego_id in juegos_unicos_anio_dado:
        # Filtrar revisiones para el juego actual y contar recomendaciones positivas
        revisiones_juego = reviews[reviews['item_id'] == juego_id]
        recomendaciones_positivas = revisiones_juego[(revisiones_juego['recommend'] == True) & (revisiones_juego['sentiment_analysis'] > 0)]
        desarrollador = juegos_anio_dado[juegos_anio_dado['item_id'] == juego_id]['developer'].iloc[0]

        # Actualizar el recuento de recomendaciones para el desarrollador
        if desarrollador in desarrolladores_por_anio:
            desarrolladores_por_anio[desarrollador] += len(recomendaciones_positivas)
        else:
            desarrolladores_por_anio[desarrollador] = len(recomendaciones_positivas)

    # Obtener el top 3 de desarrolladores con más juegos recomendados para el año dado
    top_desarrolladores = sorted(desarrolladores_por_anio.items(), key=lambda x: x[1], reverse=True)[:3]

    # Formatear los resultados en el formato requerido
    resultados = [{"Puesto {}: {}".format(idx+1, desarrollador) : juegos_recomendados} for idx, (desarrollador, juegos_recomendados) in enumerate(top_desarrolladores)]

    return resultados

# Prueba del programa
archivo_juegos = 'output_steam_games.csv'
archivo_reviews = 'user_reviews.csv'
anio_dado = 2017
resultado = obtener_top_desarrolladores_por_anio(archivo_juegos, archivo_reviews, anio_dado)
print(resultado)


[{'Puesto 1: Smartly Dressed Games': 489}, {'Puesto 2: Freejam': 142}, {'Puesto 3: Studio Wildcard,Instinct Games,Efecto Studios,Virtual Basement LLC': 104}]


#### def developer_reviews_analysis( desarrolladora : str ): Según el desarrollador, se devuelve un diccionario con el nombre del desarrollador como llave y una lista con la cantidad total de registros de reseñas de usuarios que se encuentren categorizados con un análisis de sentimiento como valor positivo o negativo.
##### Ejemplo de retorno: {'Valve' : [Negative = 182, Positive = 278]}

In [19]:
import pandas as pd

def obtener_analisis_sentimiento_por_desarrollador(archivo_juegos, archivo_reviews):
    # Cargar datos desde archivos CSV
    juegos = pd.read_csv(archivo_juegos)
    reviews = pd.read_csv(archivo_reviews)

    # Inicializar el diccionario para almacenar los resultados
    resultados = {}

    # Iterar sobre cada desarrollador
    for desarrollador in juegos['developer'].unique():
        # Obtener los item_ids asociados al desarrollador actual
        item_ids_desarrollador = juegos[juegos['developer'] == desarrollador]['item_id']
        
        # Filtrar revisiones por los item_ids del desarrollador actual
        revisiones_desarrollador = reviews[reviews['item_id'].isin(item_ids_desarrollador)]
        
        # Contar revisiones con análisis de sentimiento negativo y positivo
        revisiones_negativas = revisiones_desarrollador[revisiones_desarrollador['sentiment_analysis'] == 0]
        revisiones_positivas = revisiones_desarrollador[revisiones_desarrollador['sentiment_analysis'] == 2]
        
        # Guardar los resultados en el diccionario
        resultados[desarrollador] = {'Negative': len(revisiones_negativas), 'Positive': len(revisiones_positivas)}
    
    return resultados

# Prueba del programa
archivo_juegos = 'output_steam_games.csv'
archivo_reviews = 'user_reviews.csv'
resultado = obtener_analisis_sentimiento_por_desarrollador(archivo_juegos, archivo_reviews)
print(resultado)


{'Kotoshiro': {'Negative': 0, 'Positive': 0}, 'Secret Level SRL': {'Negative': 0, 'Positive': 0}, 'Poolians.com': {'Negative': 0, 'Positive': 0}, '彼岸领域': {'Negative': 0, 'Positive': 0}, nan: {'Negative': 0, 'Positive': 0}, 'Trickjump Games Ltd': {'Negative': 0, 'Positive': 0}, 'Poppermost Productions': {'Negative': 2, 'Positive': 8}, 'RewindApp': {'Negative': 0, 'Positive': 0}, 'Qucheza': {'Negative': 0, 'Positive': 0}, 'Stegalosaurus Game Development': {'Negative': 0, 'Positive': 0}, 'Copperpick Studio': {'Negative': 0, 'Positive': 0}, 'Ghulam Jewel': {'Negative': 0, 'Positive': 0}, 'Apillo': {'Negative': 0, 'Positive': 0}, 'Tero Lunkka': {'Negative': 0, 'Positive': 0}, 'FrozenPepper': {'Negative': 0, 'Positive': 0}, 'Casey Labrack': {'Negative': 0, 'Positive': 0}, 'Stainless Games Ltd': {'Negative': 0, 'Positive': 1}, 'Valve': {'Negative': 885, 'Positive': 3312}, 'dev4play': {'Negative': 0, 'Positive': 0}, 'BlueLine Games': {'Negative': 1, 'Positive': 0}, 'Games by Brundle': {'Negati